In [79]:
import importlib

# Imports
from rdkit import Chem
from rdkit.Chem import AllChem
import pandas as pd
from scipy.stats import zscore
import matplotlib.pyplot as plt 
import defaults
importlib.reload(defaults)

<module 'defaults' from 'C:\\Users\\20223037\\OneDrive - TU Eindhoven\\Documents\\school\\jaar2\\Biomedical\\8CC00-GroupAssignment\\defaults.py'>

In [80]:
# Read data and construct dataframe

df = pd.read_csv('datasets/tested_molecules.csv')

df.head()

SMILES  PKM2_inhibition  ERK2_inhibition
0                 C=C(C)c1nc(N)nc(N)n1                0                0
1       C=C(Cl)COc1ccc2c(C)cc(=O)oc2c1                0                0
2              C=CCNC(=O)CCCC(=O)NCC=C                0                0
3  C=CCOn1c(=O)c(C)[n+]([O-])c2ccccc21                0                0
4         C=CCn1cc(Cl)c(=O)n(CC=C)c1=O                0                0

In [81]:
# Load the dataset
df = pd.read_csv('datasets/tested_molecules.csv')  # Replace with your file path

# Function to compute descriptors
def compute_descriptors(smiles):
    mol = Chem.MolFromSmiles(smiles)
    if mol:
        return defaults.get_mol_descriptors(mol)
    else:
        return {key: None for key in defaults.x_data}

df['Descriptors'] = df['SMILES'].apply(compute_descriptors)
descriptors_df = pd.json_normalize(df['Descriptors'])
df = pd.concat([df, descriptors_df], axis=1).drop(columns=['Descriptors'])
df.head()

SMILES  PKM2_inhibition  ERK2_inhibition  \
0                 C=C(C)c1nc(N)nc(N)n1                0                0   
1       C=C(Cl)COc1ccc2c(C)cc(=O)oc2c1                0                0   
2              C=CCNC(=O)CCCC(=O)NCC=C                0                0   
3  C=CCOn1c(=O)c(C)[n+]([O-])c2ccccc21                0                0   
4         C=CCn1cc(Cl)c(=O)n(CC=C)c1=O                0                0   

   VSA_EState6  fr_nitro  NHOHCount  VSA_EState2  fr_C_O  EState_VSA4  \
0     0.000000         0          4    11.227963       0     0.000000   
1     6.779888         0          0    11.238954       0    10.949676   
2     0.000000         0          2    22.181413       2     0.000000   
3     6.777354         0          0    17.161173       0     4.730408   
4     0.000000         0          0    23.173630       0     4.567100   

   NumHAcceptors  ...  NumAromaticRings  VSA_EState1  ExactMolWt  SMR_VSA9  \
0              5  ...                 1     0.000000  151.085795  0.000000   
1              3  ...                 2    10.460706  250.039672  5.749512   
2              2  ...                 0     0.000000  210.136828  0.000000   
3              4  ...                 2     1.742245  232.084792  0.000000   
4              4  ...                 1     2.346296  226.050905  0.000000   

   NumHDonors     BertzCT  FpDensityMorgan2  SMR_VSA10  FractionCSP3  \
0           2  272.774159          1.636364  17.469783      0.166667   
1           0  628.087447          2.235294  22.570184      0.153846   
2           2  212.742421          1.333333  11.814359      0.454545   
3           0  631.418725          2.235294  11.033401      0.166667   
4           0  499.124344          1.866667  11.600940      0.200000   

   fr_nitro_arom  
0              0  
1              0  
2              0  
3              0  
4              0  

[5 rows x 79 columns]

In [82]:
# Convert SMILES to fingerprints, so we have usable data training

def smiles_to_fingerprint(smiles):
    mol = Chem.MolFromSmiles(smiles)
    if mol:
        fp = AllChem.GetMorganFingerprintAsBitVect(mol, 2, nBits=1024)
        return list(fp)
    else:
        return [0] * 1024
    
df['Fingerprint'] = df['SMILES'].apply(smiles_to_fingerprint)

df.head()

SMILES  PKM2_inhibition  ERK2_inhibition  \
0                 C=C(C)c1nc(N)nc(N)n1                0                0   
1       C=C(Cl)COc1ccc2c(C)cc(=O)oc2c1                0                0   
2              C=CCNC(=O)CCCC(=O)NCC=C                0                0   
3  C=CCOn1c(=O)c(C)[n+]([O-])c2ccccc21                0                0   
4         C=CCn1cc(Cl)c(=O)n(CC=C)c1=O                0                0   

   VSA_EState6  fr_nitro  NHOHCount  VSA_EState2  fr_C_O  EState_VSA4  \
0     0.000000         0          4    11.227963       0     0.000000   
1     6.779888         0          0    11.238954       0    10.949676   
2     0.000000         0          2    22.181413       2     0.000000   
3     6.777354         0          0    17.161173       0     4.730408   
4     0.000000         0          0    23.173630       0     4.567100   

   NumHAcceptors  ...  VSA_EState1  ExactMolWt  SMR_VSA9  NumHDonors  \
0              5  ...     0.000000  151.085795  0.000000           2   
1              3  ...    10.460706  250.039672  5.749512           0   
2              2  ...     0.000000  210.136828  0.000000           2   
3              4  ...     1.742245  232.084792  0.000000           0   
4              4  ...     2.346296  226.050905  0.000000           0   

      BertzCT  FpDensityMorgan2  SMR_VSA10  FractionCSP3  fr_nitro_arom  \
0  272.774159          1.636364  17.469783      0.166667              0   
1  628.087447          2.235294  22.570184      0.153846              0   
2  212.742421          1.333333  11.814359      0.454545              0   
3  631.418725          2.235294  11.033401      0.166667              0   
4  499.124344          1.866667  11.600940      0.200000              0   

                                         Fingerprint  
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1  [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, ...  
2  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  

[5 rows x 80 columns]

In [83]:
column_names = defaults.x_data
z_scores = df[defaults.x_data].apply(zscore)
rows_names = defaults.y_data

threshold = 2
lower_threshold = -2

# Create subplots for each variable
fig, axs = plt.subplots(len(column_names), len(rows_names), figsize=(20, len(column_names)*6))

for i, inhibition_enzyme in enumerate(defaults.y_data):
    # Iterate over each variable name
    for j, column_name in enumerate(column_names):
        # Compute z-scores for the specified column
        #z_scores = df[column_name].apply(zscore)
        
        # Extract the column values for PKM2_inhibition
        PKM2_inhibition = df[inhibition_enzyme]
        
        # Identify outliers based on z-scores exceeding the thresholds
        outliers = (z_scores.abs() > threshold).any(axis=1)
        
        # Extract z-scores for the column of interest
        z_scores_column = z_scores[column_name]
        
        # Define colors for the bars based on the ratio
        colors = PKM2_inhibition.map({0: 'skyblue', 1: 'orange'})
        
        # Plotting the histogram as a stacked bar histogram
        axs[j][i].hist(z_scores_column[PKM2_inhibition == 0], bins=80, color='skyblue', edgecolor='black', alpha=0.7, label=f'{column_name} = 0', stacked=True)
        axs[j][i].hist(z_scores_column[PKM2_inhibition == 1], bins=80, color='orange', edgecolor='black', alpha=0.7, label=f'{column_name} = 1', stacked=True)
        
        # Enhancing plot aesthetics and providing descriptive labels
        axs[j][i].set_title(f'Stacked Distribution of Standardized {column_name} Values based on {inhibition_enzyme}')
        axs[j][i].set_xlabel('Standardized LogP')
        axs[j][i].set_ylabel('Frequency')
        
        # Add vertical lines at the thresholds for visual reference
        axs[j][i].axvline(x=threshold, color='red', linestyle='--', label=f'Threshold ({threshold})')
        axs[j][i].axvline(x=lower_threshold, color='green', linestyle='--', label=f'Lower Threshold ({lower_threshold})')
        
        # Indicate the presence of the thresholds
        axs[j][i].text(threshold + 0.1, axs[j][i].get_ylim()[1] * 0.9, 'Upper Threshold', color='red')
        axs[j][i].text(lower_threshold - 0.5, axs[j][i].get_ylim()[1] * 0.9, 'Lower Threshold', color='green')
        
        # Add a legend
        axs[j][i].legend()

plt.tight_layout()
plt.show()

In [84]:
# change outliers to NaN
df1 = df[defaults.x_data]

mask = (z_scores.abs() > 2)
mask.head()

df1[mask] = pd.NA

df1.head()

C:\Users\20223037\AppData\Local\Temp\ipykernel_1736\676677244.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1[mask] = pd.NA
C:\Users\20223037\AppData\Local\Temp\ipykernel_1736\676677244.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1[mask] = pd.NA


VSA_EState6  fr_nitro  NHOHCount  VSA_EState2  fr_C_O  EState_VSA4  \
0     0.000000       0.0        NaN    11.227963     0.0     0.000000   
1     6.779888       0.0        0.0    11.238954     0.0    10.949676   
2     0.000000       0.0        2.0    22.181413     2.0     0.000000   
3     6.777354       0.0        0.0    17.161173     0.0     4.730408   
4     0.000000       0.0        0.0    23.173630     0.0     4.567100   

   NumHAcceptors  VSA_EState9  fr_amide  fr_alkyl_halide  ...  \
0            5.0          0.0       0.0              0.0  ...   
1            3.0          0.0       0.0              0.0  ...   
2            2.0          0.0       2.0              0.0  ...   
3            4.0          0.0       0.0              0.0  ...   
4            4.0          0.0       0.0              0.0  ...   

   NumAromaticRings  VSA_EState1  ExactMolWt  SMR_VSA9  NumHDonors  \
0               1.0     0.000000         NaN  0.000000         2.0   
1               2.0    10.460706  250.039672  5.749512         0.0   
2               NaN     0.000000  210.136828  0.000000         2.0   
3               2.0     1.742245  232.084792  0.000000         0.0   
4               1.0     2.346296  226.050905  0.000000         0.0   

      BertzCT  FpDensityMorgan2  SMR_VSA10  FractionCSP3  fr_nitro_arom  
0         NaN          1.636364  17.469783      0.166667            0.0  
1  628.087447          2.235294  22.570184      0.153846            0.0  
2         NaN               NaN  11.814359      0.454545            0.0  
3  631.418725          2.235294  11.033401      0.166667            0.0  
4  499.124344          1.866667  11.600940      0.200000            0.0  

[5 rows x 76 columns]

In [85]:
z_scores.head()

VSA_EState6  fr_nitro  NHOHCount  VSA_EState2    fr_C_O  EState_VSA4  \
0    -1.893256 -0.029948   2.860692    -0.735192 -1.255262    -1.263651   
1    -0.590407 -0.029948  -1.220526    -0.734223 -1.255262    -0.540224   
2    -1.893256 -0.029948   0.820083     0.230569  1.022579    -1.263651   
3    -0.590894 -0.029948  -1.220526    -0.212063 -1.255262    -0.951121   
4    -1.893256 -0.029948  -1.220526     0.318053 -1.255262    -0.961910   

   NumHAcceptors  VSA_EState9  fr_amide  fr_alkyl_halide  ...  \
0      -0.007504    -0.102789 -0.978965        -0.191223  ...   
1      -1.124038    -0.102789 -0.978965        -0.191223  ...   
2      -1.682305    -0.102789  1.294760        -0.191223  ...   
3      -0.565771    -0.102789 -0.978965        -0.191223  ...   
4      -0.565771    -0.102789 -0.978965        -0.191223  ...   

   NumAromaticRings  VSA_EState1  ExactMolWt  SMR_VSA9  NumHDonors   BertzCT  \
0         -1.310474    -0.962505   -2.735087 -0.816254    1.108443 -2.135923   
1         -0.282723    -0.239185   -1.356857 -0.000897   -1.295877 -0.760753   
2         -2.338224    -0.962505   -1.912624 -0.816254    1.108443 -2.368264   
3         -0.282723    -0.842035   -1.606932 -0.816254   -1.295877 -0.747860   
4         -1.310474    -0.800267   -1.690972 -0.816254   -1.295877 -1.259879   

   FpDensityMorgan2  SMR_VSA10  FractionCSP3  fr_nitro_arom  
0         -1.089142  -0.430402     -0.934815      -0.029948  
1          1.544660   0.040364     -1.010806      -0.029948  
2         -2.421721  -0.952396      0.771521      -0.029948  
3          1.544660  -1.024479     -0.934815      -0.029948  
4         -0.076382  -0.972095     -0.737239      -0.029948  

[5 rows x 76 columns]

In [86]:
fingerprint_data = df['SMILES'].apply(smiles_to_fingerprint)

finger_print = pd.DataFrame(fingerprint_data)

finger_print.head()
df2 = pd.DataFrame(finger_print['SMILES'].to_list(), columns=[f'Fingerprint_{i}' for i in range(len(finger_print['SMILES'][0]))])

merged_df = pd.concat([df2, df1, df], axis=1)
merged_df.head(50)

Fingerprint_0  Fingerprint_1  Fingerprint_2  Fingerprint_3  Fingerprint_4  \
0               0              0              0              0              0   
1               0              0              0              1              0   
2               0              0              0              0              0   
3               0              0              0              0              0   
4               0              0              0              0              0   
5               0              0              0              0              0   
6               0              0              0              0              0   
7               0              0              0              0              0   
8               0              1              0              0              0   
9               0              1              0              0              0   
10              0              1              0              0              0   
11              0              0              0              0              0   
12              0              1              0              0              0   
13              0              0              0              0              0   
14              0              0              0              0              0   
15              0              0              0              0              0   
16              0              0              0              0              0   
17              0              0              0              0              0   
18              0              0              0              0              0   
19              0              0              0              0              0   
20              0              0              0              0              0   
21              0              0              0              0              0   
22              0              0              0              0              0   
23              0              0              0              0              0   
24              0              0              0              0              0   
25              0              0              0              0              0   
26              0              0              0              0              0   
27              0              0              0              0              0   
28              0              0              0              0              0   
29              0              0              0              0              0   
30              0              0              0              0              0   
31              0              0              0              1              0   
32              0              0              0              0              1   
33              0              0              0              0              0   
34              0              0              0              0              0   
35              0              0              0              0              0   
36              0              0              0              0              0   
37              0              0              0              0              0   
38              0              0              0              0              0   
39              0              1              0              0              0   
40              0              0              0              0              0   
41              0              0              0              0              0   
42              0              0              0              0              0   
43              0              0              0              0              0   
44              0              0              0              0              0   
45              0              0              0              0              0   
46              0              0              0              0              0   
47              0              0              0              0              1   
48              0              0   

In [87]:
# Remove columns that have a Nah
dropped_df = merged_df.dropna()

In [88]:
dropped_df.to_csv('./datasets/prepared_data.csv')